# How to view previous jobs and retrieve results

**Viewing metadata and retrieving results from jobs previously submitted to Fire Opal**

Fire Opal allows you to view a list of previous jobs with metadata and to retrieve results from previously submitted jobs.

**_Note: To achieve the highest degree of accuracy, be sure to always retrieve results directly from Fire Opal. Results obtained from hardware providers' platforms and SDKs will not include Fire Opal's post-processing will therefore be of lower quality._** 

In this guide, you will learn how to:

1. Retrieve results or status from a FireOpalJob object.
1. View and filter a list of previous jobs.
1. Use a job's unique ID to retrieve the results.
1. Get a list of job metadata.

### 1. Poll for results or get status from a FireOpalJob object

Fire Opal's job execution functions (`execute`, `iterate`, and `solve_qaoa`) work asynchronously and return a `FireOpalJob` object. You can use this job object to poll for results synchronously while the job is processing, query the job's status, and retrieve results once the job has completed.

In [ ]:
import fireopal as fo

In [ ]:
# Run a circuit execution job
fire_opal_job = fo.execute(...)

You can use this `FireOpalJob` object to query the job's status.

In [ ]:
print(fire_opal_job.status())

{'status_message': 'Job has been submitted to Q-CTRL.',
 'action_status': 'STARTED'}

You can use `.result()` to poll for the job results if the job is still processing or to retrieve results once the job has finished.

In [ ]:
# Poll for results synchronously
fire_opal_results = job.result()

### 2. View list of previous jobs and metadata

To view pre-formatted metadata, use the `activity_monitor` function. As shown below, this function's default behavior is to display metadata from the most recent job.

In [2]:
from fireopal import activity_monitor

In [3]:
activity_monitor()

Getting jobs for all statuses. To filter jobs by status,  use the status keyword argument. Valid status values are: SUCCESS, FAILURE, REVOKED, PENDING, RECEIVED, RETRY, STARTED.

| Function | Status  | Created at (UTC)    | Updated at (UTC)    | Action ID |
| -------- | ------- | ------------------- | ------------------- | --------- |
| execute  | STARTED | 2023-10-10 18:12:24 | 2023-10-10 18:12:25 | 1824870   |


To view metadata for more than one job, use the `limit` parameter. For example, the code below displays the five most recent jobs.

In [4]:
activity_monitor(limit=5)

Getting jobs for all statuses. To filter jobs by status,  use the status keyword argument. Valid status values are: SUCCESS, FAILURE, REVOKED, PENDING, RECEIVED, RETRY, STARTED.

| Function | Status  | Created at (UTC)    | Updated at (UTC)    | Action ID |
| -------- | ------- | ------------------- | ------------------- | --------- |
| execute  | STARTED | 2023-10-10 18:12:24 | 2023-10-10 18:12:25 | 1824870   |
| validate | SUCCESS | 2023-10-10 18:12:10 | 2023-10-10 18:12:17 | 1824869   |
| execute  | STARTED | 2023-10-10 17:52:27 | 2023-10-10 17:52:27 | 1824868   |
| execute  | FAILURE | 2023-10-10 17:51:12 | 2023-10-10 17:51:17 | 1824867   |
| validate | SUCCESS | 2023-10-10 17:50:16 | 2023-10-10 17:50:25 | 1824866   |


To only view older jobs, the `offset` parameter can be used to skip more recent jobs. For example, the code below skips the five most recent jobs and views the sixth most recent.

In [5]:
activity_monitor(limit=1, offset=5)

Getting jobs for all statuses. To filter jobs by status,  use the status keyword argument. Valid status values are: SUCCESS, FAILURE, REVOKED, PENDING, RECEIVED, RETRY, STARTED.

| Function | Status  | Created at (UTC)    | Updated at (UTC)    | Action ID |
| -------- | ------- | ------------------- | ------------------- | --------- |
| validate | SUCCESS | 2023-10-10 16:45:53 | 2023-10-10 16:45:59 | 1824865   |


As the outputs above indicate, we can also filter by status.

In [14]:
activity_monitor(limit=4, status="SUCCESS")

| Function | Status  | Created at (UTC)    | Updated at (UTC)    | Action ID |
| -------- | ------- | ------------------- | ------------------- | --------- |
| validate | SUCCESS | 2023-10-10 18:12:10 | 2023-10-10 18:12:17 | 1824869   |
| validate | SUCCESS | 2023-10-10 17:50:16 | 2023-10-10 17:50:25 | 1824866   |
| validate | SUCCESS | 2023-10-10 16:45:53 | 2023-10-10 16:45:59 | 1824865   |
| validate | SUCCESS | 2023-10-10 16:34:13 | 2023-10-10 16:34:18 | 1824864   |


### 3. Use a job's ID to retrieve results

The results of a successfully completed job can be retrieved by passing its ID to the `get_result` function.

**_Note: Only jobs that have completed successfully can be queried for results. Be sure to leave your jobs running for them to finish executing. Even in the case of kernel disconnection, the job will still complete, and results can later be retrieved._** 

In [15]:
import warnings

job_id = "YOUR_JOB_ID"

# The get_result function will display any runtime warnings
# captured during the function call that generated the job.
# We suppress them here for brevity.
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    result = fo.get_result(job_id)

print(result)

{'results': [{'000000': 0.013513385402017056, '000001': 0.0012759565358072978, '000011': 0.0036011607913108822, '000111': 0.006893546308909863, '011111': 0.0024122040902233247, '100111': 0.0028186530910052215, '110111': 0.003930582858170521, '111110': 0.031615686168495, '111111': 0.9339388247540609}]}


### 4. Get a list of job metadata


Finally, note that it's possible to instead retrieve information (metadata) about the job, such as the job status or time of creation. To do so, use the `get_action_metadata` function, which supports the same parameters as the `activity_monitor` and returns a list, as shown in the following example.

In [31]:
metadata = fo.get_action_metadata(limit=4, offset=37, status="SUCCESS")

# Each list element is an ActionMetadata instance, which is just a dataclass.
print(metadata[0])
print("\n")

# Like any dataclass, we can access the attribute values through dot notation.
print(
    f"Function name: {metadata[0].name}\n"
    f"Job status: {metadata[0].status}\n"
    f"Job created at: {metadata[0].created_at}\n"
    f"Job updated at: {metadata[0].updated_at}\n"
    f"Action ID: {metadata[0].model_id}"
)

ActionMetadata(name='execute', status='SUCCESS', created_at='2023-07-21 16:11:11', updated_at='2023-07-22 01:05:39', model_id='1759672')


Function name: execute
Job status: SUCCESS
Job created at: 2023-07-21 16:11:11
Job updated at: 2023-07-22 01:05:39
Action ID: 1759672


Now that you know how to view previous jobs and retrieve results, try [creating and running circuits](https://docs.q-ctrl.com/fire-opal/tutorials/creating-and-running-circuits) and you'll be able to retrieve the results at your convenience.

In [1]:
from fireopal import print_package_versions

print_package_versions()

| Package               | Version |
| --------------------- | ------- |
| Python                | 3.10.11 |
| networkx              | 2.8.8   |
| numpy                 | 1.26.0  |
| sympy                 | 1.12    |
| fire-opal             | 6.3.0   |
| qctrl-workflow-client | 1.2.0   |
